In [1]:
import requests
from bs4 import BeautifulSoup

In [2]:
# URL of the page to scrape
url = "https://www.tijorifinance.com/company/reliance-industries-limited/"

# Headers to mimic a browser request
headers = {
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36"
}

In [3]:
# Send a GET request to the page with headers
response = requests.get(url, headers=headers)
response.raise_for_status()  # Check if the request was successful

In [4]:
# Parse the page content
soup = BeautifulSoup(response.content, "html.parser")

In [6]:
# Example: Scraping company name and key data points
company_name = soup.find("h1").text.strip()
company_name

'Reliance Industries Ltd.'

In [11]:
divs = soup.find_all('div')
divs

[<div aria-hidden="true" aria-labelledby="modalChartPopUpCenterTitle" class="modal fade" id="feedbackChartPopUp" role="dialog" tabindex="-1">
 <div class="modal-dialog modal-dialog-centered" role="document">
 <div class="modal-content">
 <div class="modal-body" id="modalpop-chart">
 <form class="myfomr2 formcallbackForm form_callback" id="form_callback" method="post">
 <div class="feedbackheading">
 Leave Feedback
 </div>
 <div class="feedbacksubheading">
 We'd love to hear from you!
 </div>
 <div class="form-group">
 <label class="formheading">
 Name<span class="mandatory">*</span>
 </label>
 <input class="form-control" id="form_callback_name" name="fname" required=""/>
 </div>
 <div class="form-group">
 <label class="formheading">
 Email
 </label>
 <input class="form-control" id="form_callback_email" name="email" placeholder="To help us get in touch with you" type="email"/>
 </div>
 <div class="form-group">
 <label class="formheading">
 Message<span class="mandatory">*</span>
 </labe

In [8]:
# Find all <a> tags with class 'btn' and href starting with '/company/'
a_tags = soup.find_all('a', class_='btn', href=True)

In [9]:
# Filter the <a> tags by href pattern
matching_a_tags = [a for a in a_tags if a['href'].startswith('/company/')]

In [10]:
# Extract and print the href and content of each matching <a> tag
for a in matching_a_tags:
    href = a['href']
    content = a.get_text(strip=True)
    print(f"Content: {content}, Href: {href}")

Content: CG Power and Industrial Solutions Ltd. (11), Href: /company/crompton-greaves-limited
Content: Indus Towers Ltd. (7), Href: /company/bharti-infratel-limited
Content: Thermax Ltd. (7), Href: /company/thermax-limited
Content: Dixon Technologies (India) Ltd. (11), Href: /company/dixon-technologies-limited
Content: KEI Industries Ltd. (23), Href: /company/kei-industries-limited
Content: Deepak Nitrite Ltd. (18), Href: /company/deepak-nitrite-limited
Content: Aegis Logistics Ltd. (12), Href: /company/aegis-logistics-limited
Content: Jupiter Wagons Ltd. (12), Href: /company/commercial-engineers-body-builders-company-limited
Content: Tejas Networks Ltd. (13), Href: /company/tejas-networks-limited
Content: NCC Ltd. (3), Href: /company/ncc-limited
Content: Jindal Saw Ltd. (97), Href: /company/jindal-saw-limited
Content: Welspun Corp Ltd. (25), Href: /company/welspun-corp-limited
Content: Olectra Greentech Ltd. (2), Href: /company/goldstone-infratech-limited
Content: Maharashtra Seamless

In [9]:
import re
import json

# Extract suppliers and the companies they supply to
supplier_data = []

# Find the section containing suppliers
suppliers_section = soup.find('section', id='suppliers')

if suppliers_section:
    # Find all supplier entries
    supplier_entries = suppliers_section.find_all('div', id=re.compile(r'card_heading_suppliers'))

    for entry in supplier_entries:
        supplier_name = entry.find('a', class_='btn').text.strip()
        supplier_href = entry.find('a', class_='btn')['href']
        companies_supplied_to = []

        # Find the associated companies supplied to by the supplier
        collapse_div = entry.find_next_sibling('div', class_='collapse')
        if collapse_div:
            companies = collapse_div.find_all('a', class_='company_page_link')
            for company in companies:
                company_name = company.text.strip()
                company_href = company['href']
                companies_supplied_to.append({'name': company_name, 'href': company_href})

        supplier_data.append({'name': supplier_name, 'href': supplier_href, 'supplies_to': companies_supplied_to})

# Print the extracted data in a prettified format
# print(json.dumps(supplier_data, indent=4))


In [ ]:
import networkx as nx
import matplotlib.pyplot as plt

# Sample supplier data
# supplier_data = [
#     {
#         'name': 'CG Power and Industrial Solutions Ltd.',
#         'href': '/company/crompton-greaves-limited',
#         'supplies_to': [
#             {'name': 'ABB India Ltd.', 'href': '/company/abb-india-limited/'},
#             {'name': 'Ambuja Cements Ltd.', 'href': '/company/ambuja-cements-limited/'},
#             {'name': 'Bharat Petroleum Corporation Ltd.', 'href': '/company/bharat-petroleum-corporation-limited/'},
#             # More companies...
#         ]
#     },
#     {
#         'name': 'TATA',
#         'href': '/company/tata-limited',
#         'supplies_to': [
#             {'name': 'India Ltd.', 'href': '/company/india-limited/'},
#             {'name': 'Ambuja Cements Ltd.', 'href': '/company/ambuja-cements-limited/'},
#             {'name': 'Bharat Petroleum Corporation Ltd.', 'href': '/company/bharat-petroleum-corporation-limited/'},
#             # More companies...
#         ]
#     },
#     {
#         'name': 'ADANI',
#         'href': '/company/adani-limited',
#         'supplies_to': [
#             {'name': 'India Ltd.', 'href': '/company/india-limited/'},
#             {'name': 'Ambuja Cements Ltd.', 'href': '/company/ambuja-cements-limited/'},
#             {'name': 'TATA', 'href': '/company/tata-limited/'},
#             # More companies...
#         ]
#     }
#     # More suppliers...
# ]

# Create a directed graph
G = nx.DiGraph()

# Add nodes and edges
for supplier in supplier_data:
    supplier_name = supplier['name']
    G.add_node(supplier_name, type='supplier')
    for company in supplier['supplies_to']:
        company_name = company['name']
        G.add_node(company_name, type='customer')
        G.add_edge(supplier_name, company_name)

# Set node colors based on type
node_colors = ['red' if node[1]['type'] == 'supplier' else 'blue' for node in G.nodes(data=True)]

# Draw the graph
plt.figure(figsize=(2^15, 2^15))
pos = nx.spring_layout(G)
nx.draw(G, pos, with_labels=True, node_color=node_colors, node_size=300, font_size=10, font_color='white', font_weight='bold', edge_color='gray')

# Add a legend
plt.legend(['Supplier', 'Customer'], loc='upper left')

plt.title('Supplier-Customer Relationships')
plt.show()


In [ ]:
import plotly.graph_objects as go
import networkx as nx

# Sample supplier data
# supplier_data = [
#     {
#         'name': 'CG Power and Industrial Solutions Ltd.',
#         'href': '/company/crompton-greaves-limited',
#         'supplies_to': [
#             {'name': 'ABB India Ltd.', 'href': '/company/abb-india-limited/'},
#             {'name': 'Ambuja Cements Ltd.', 'href': '/company/ambuja-cements-limited/'},
#             {'name': 'Bharat Petroleum Corporation Ltd.', 'href': '/company/bharat-petroleum-corporation-limited/'},
#             # More companies...
#         ]
#     },
#     {
#         'name': 'TATA',
#         'href': '/company/tata-limited',
#         'supplies_to': [
#             {'name': 'India Ltd.', 'href': '/company/india-limited/'},
#             {'name': 'Ambuja Cements Ltd.', 'href': '/company/ambuja-cements-limited/'},
#             {'name': 'Bharat Petroleum Corporation Ltd.', 'href': '/company/bharat-petroleum-corporation-limited/'},
#             # More companies...
#         ]
#     },
#     {
#         'name': 'ADANI',
#         'href': '/company/adani-limited',
#         'supplies_to': [
#             {'name': 'India Ltd.', 'href': '/company/india-limited/'},
#             {'name': 'Ambuja Cements Ltd.', 'href': '/company/ambuja-cements-limited/'},
#             {'name': 'TATA', 'href': '/company/tata-limited/'},
#             # More companies...
#         ]
#     }
#     # More suppliers...
# ]

# Create a directed graph
G = nx.DiGraph()

# Add nodes and edges to the graph
for supplier in supplier_data:
    supplier_name = supplier['name']
    G.add_node(supplier_name, type='supplier')
    for customer in supplier['supplies_to']:
        customer_name = customer['name']
        G.add_node(customer_name, type='customer')
        G.add_edge(supplier_name, customer_name)

# Define node colors based on type
node_colors = {'supplier': 'red', 'customer': 'blue'}
colors = [node_colors[G.nodes[node]['type']] for node in G.nodes]

# Create position layout for the nodes
pos = nx.spring_layout(G)

# Create edge traces
edge_trace = go.Scatter(
    x=[],
    y=[],
    line=dict(width=0.5, color='#888'),
    hoverinfo='none',
    mode='lines'
)

for edge in G.edges():
    x0, y0 = pos[edge[0]]
    x1, y1 = pos[edge[1]]
    edge_trace['x'] += (x0, x1, None)
    edge_trace['y'] += (y0, y1, None)

# Create node traces
node_trace = go.Scatter(
    x=[],
    y=[],
    text=[],
    mode='markers+text',
    textposition='top center',
    hoverinfo='text',
    marker=dict(
        showscale=True,
        colorscale='YlGnBu',
        size=10,
        color=[],
        colorbar=dict(
            thickness=15,
            title='Node Connections',
            xanchor='left',
            titleside='right'
        ),
        line_width=2
    )
)

for node in G.nodes():
    x, y = pos[node]
    node_trace['x'] += (x,)
    node_trace['y'] += (y,)
    node_trace['marker']['color'] += ([colors.pop(0)],)
    node_info = f"{node} ({G.nodes[node]['type']})"
    node_trace['text'] += ([node_info],)

# Create the figure
fig = go.Figure(data=[edge_trace, node_trace],
                layout=go.Layout(
                    title='Supplier-Customer Relationships',
                    titlefont_size=16,
                    showlegend=False,
                    hovermode='closest',
                    margin=dict(b=20, l=5, r=5, t=40),
                    annotations=[dict(
                        text="Supplier-Customer Network",
                        showarrow=False,
                        xref="paper", yref="paper",
                        x=0.005, y=-0.002
                    )],
                    xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                    yaxis=dict(showgrid=False, zeroline=False, showticklabels=False))
                )

# Show the figure
fig.show()
